In [1]:
import librosa
import pandas as pd #processing csv files
import numpy as np
# import matplotlib.pyplot as plt
# %matplotlib inline
import os
# from PIL import Image
import pathlib
import csv
from IPython.display import Audio

from sklearn.svm import SVC
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelEncoder, StandardScaler

In [ ]:
header = 'poly_features chroma_cens chroma_cqt chroma_stft tempogram spectral_centroid spectral_bandwidth spectral_rolloff spectral_contrast spectral_flatness zero_crossing_rate rmse'
for i in range(1, 31):
    header += f' mfcc{i}'
header += ' label'
header = header.split()

In [ ]:
file = open('data.csv', 'w', newline='')
with file:
    writer = csv.writer(file)
    writer.writerow(header)

genres = 'blues classical country disco hiphop jazz metal pop reggae rock'.split()
    
for genre in genres:
    for filename in os.listdir(f'./genres/{genre}'):
        song = f'./genres/{genre}/{filename}'
        print("Featuring file {}".format(song))
        y, sr = librosa.load(song)
        
        mfcc = librosa.feature.mfcc(y, n_mfcc=30)
        poly_features = librosa.feature.poly_features(y)
        chroma_cens = librosa.feature.chroma_cens(y)
        chroma_cqt = librosa.feature.chroma_cqt(y)
        chroma_stft = librosa.feature.chroma_stft(y)
        tempogram = librosa.feature.tempogram(y)
        
        spectral_centroid = librosa.feature.spectral_centroid(y)
        spectral_bandwitdh = librosa.feature.spectral_bandwidth(y)
        spectral_rolloff = librosa.feature.spectral_rolloff(y)
        spectral_contrast = librosa.feature.spectral_contrast(y)
        spectral_flatness = librosa.feature.spectral_flatness(y)
        zero_crossing_rate = librosa.feature.zero_crossing_rate(y)
        
        rmse = librosa.feature.rmse(y)
        
        tmp = ""
        
        tmp = f'{np.mean(poly_features)} {np.mean(chroma_cens)} {np.mean(chroma_cqt)} {np.mean(chroma_stft)} {np.mean(tempogram)} {np.mean(spectral_centroid)} {np.mean(spectral_bandwitdh)} {np.mean(spectral_rolloff)} {np.mean(spectral_contrast)} {np.mean(spectral_flatness)} {np.mean(zero_crossing_rate)} {np.mean(rmse)}'
        
        for i in mfcc:
            tmp += f' {np.mean(i)}'
        tmp += f' {genre}'
        
        file = open('data.csv', 'a', newline='')
        with file:
            writer = csv.writer(file)
            writer.writerow(tmp.split())

In [2]:
loadFile = pd.read_csv("data.csv")
loadFile.head(5)

poly_features  chroma_cens  chroma_cqt  chroma_stft  tempogram  \
0       1.229859     0.261270    0.493245     0.330231   0.172176   
1       1.309781     0.249554    0.441091     0.377614   0.132772   
2       1.108768     0.220857    0.360411     0.253553   0.179737   
3       1.385195     0.278472    0.538004     0.429437   0.194486   
4       2.194832     0.279882    0.595658     0.405839   0.135366   

   spectral_centroid  spectral_bandwidth  spectral_rolloff  spectral_contrast  \
0        2840.060761         2444.189468       5711.836175          23.108857   
1        1612.514945         1971.623034       3468.319553          22.560196   
2        1330.715617         1973.410538       2898.788813          27.930864   
3        1739.134033         2290.407132       4551.141570          21.936154   
4        2235.589429         2099.812076       4389.434375          21.913586   

   spectral_flatness  ...     mfcc22     mfcc23     mfcc24    mfcc25  \
0           0.011075  ...  -4.124760  -6.276230   0.185397 -2.974018   
1           0.002966  ...  -0.541779  -3.622599  -6.595345 -5.301505   
2           0.000580  ... -15.297078 -13.744897 -16.158301 -5.241371   
3           0.001698  ...  -7.017246  -3.793741  -6.260772 -2.578779   
4           0.005862  ...   1.069546  -0.854068   1.921638  3.248943   

      mfcc26    mfcc27     mfcc28    mfcc29    mfcc30  label  
0  -1.936639 -3.962446  -4.655244  0.989061 -8.420364  blues  
1  -3.725492 -6.659377  -3.406073 -3.216296 -4.054273  blues  
2 -11.314185 -9.463752 -14.037280 -6.320993 -2.198424  blues  
3  -5.917237 -6.961733  -5.913039 -2.994708 -5.058941  blues  
4  -2.130625  8.221537   0.378400 -4.359388  0.063865  blues  

[5 rows x 43 columns]

In [3]:
genre_list = loadFile.iloc[:,-1]
encoder = LabelEncoder()
y = encoder.fit_transform(genre_list)

In [4]:
X_train, X_test, y_train, y_test = train_test_split(loadFile.iloc[:,:-1], y, test_size=0.2)

In [5]:
scale = StandardScaler()
X = scale.fit_transform(X_train)

In [6]:
model = SVC()
model.fit(X, y_train)
# model = GaussianNB()
# model.fit(X, y_train)

SVC(C=1.0, cache_size=200, class_weight=None, coef0=0.0,
  decision_function_shape='ovr', degree=3, gamma='auto', kernel='rbf',
  max_iter=-1, probability=False, random_state=None, shrinking=True,
  tol=0.001, verbose=False)

In [7]:
test_sample = scale.transform(X_test)
model.score(test_sample, y_test)

0.745

In [8]:
def feature_audio_file(file_path):
    header = 'poly_features chroma_cens chroma_cqt chroma_stft tempogram spectral_centroid spectral_bandwidth spectral_rolloff spectral_contrast spectral_flatness zero_crossing_rate rmse'
    for i in range(1, 31):
        header += f' mfcc{i}'
    header = header.split()

    file = open('test.csv', 'w', newline='')
    with file:
        writer = csv.writer(file)
        writer.writerow(header)


    y, sr = librosa.load(file_path)

    mfcc = librosa.feature.mfcc(y, n_mfcc=30)
    poly_features = librosa.feature.poly_features(y)
    chroma_cens = librosa.feature.chroma_cens(y)
    chroma_cqt = librosa.feature.chroma_cqt(y)
    chroma_stft = librosa.feature.chroma_stft(y)
    tempogram = librosa.feature.tempogram(y)

    spectral_centroid = librosa.feature.spectral_centroid(y)
    spectral_bandwitdh = librosa.feature.spectral_bandwidth(y)
    spectral_rolloff = librosa.feature.spectral_rolloff(y)
    spectral_contrast = librosa.feature.spectral_contrast(y)
    spectral_flatness = librosa.feature.spectral_flatness(y)
    zero_crossing_rate = librosa.feature.zero_crossing_rate(y)

    rmse = librosa.feature.rmse(y)

    tmp = ""

    tmp = f'{np.mean(poly_features)} {np.mean(chroma_cens)} {np.mean(chroma_cqt)} {np.mean(chroma_stft)} {np.mean(tempogram)} {np.mean(spectral_centroid)} {np.mean(spectral_bandwitdh)} {np.mean(spectral_rolloff)} {np.mean(spectral_contrast)} {np.mean(spectral_flatness)} {np.mean(zero_crossing_rate)} {np.mean(rmse)}'

    for i in mfcc:
        tmp += f' {np.mean(i)}'

    file = open('test.csv', 'a', newline='')
    with file:
        writer = csv.writer(file)
        writer.writerow(tmp.split())

In [15]:
Audio('test_data/file1.mp3')

In [17]:
feature_audio_file("test_data/file1.mp3")
testFile = pd.read_csv("test.csv")
testFile.head(5)

poly_features  chroma_cens  chroma_cqt  chroma_stft  tempogram  \
0       2.331544     0.265274    0.540807      0.46102   0.135516   

   spectral_centroid  spectral_bandwidth  spectral_rolloff  spectral_contrast  \
0        2906.957441          2911.47948       6403.329007          19.289003   

   spectral_flatness  ...    mfcc21    mfcc22    mfcc23    mfcc24    mfcc25  \
0           0.046323  ... -3.125959  3.540976 -4.648682  4.366893 -2.131054   

     mfcc26    mfcc27    mfcc28    mfcc29    mfcc30  
0 -1.266838 -5.671553 -0.684516 -0.586868  3.298156  

[1 rows x 42 columns]

In [18]:
Z = scale.transform(np.array(testFile.iloc[:,:], dtype=float))
result = model.predict(Z)
genresArr = ['blues', 'classical', 'country', 'disco', 'hiphop', 'jazz', 'metal', 'pop', 'reggae', 'rock']
print(genresArr[result[0]])

hiphop
